In [2]:
%run Requirements.ipynb

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/06/04 17:11:36 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
24/06/04 17:11:37 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


In [3]:
df = spark.sql(
    """
    SELECT DISTINCT SM.Artists
    FROM PARQUET.`/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/AppleMusic` AS AM
    INNER JOIN PARQUET.`/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/SpotifyMusic` AS SM 
    ON LTRIM(RTRIM(LOWER(AM.`Artist Name`))) = LTRIM(RTRIM(LOWER(SM.Artists)))
    LEFT JOIN PARQUET.`/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/YoutubeMusic` AS YM
    ON LTRIM(RTRIM(LOWER(AM.`Artist Name`))) = LTRIM(RTRIM(LOWER(YM.`Artist Name`)))
    """
)

24/06/04 17:11:42 WARN HiveConf: HiveConf of name hive.stats.jdbc.timeout does not exist
24/06/04 17:11:42 WARN HiveConf: HiveConf of name hive.stats.retries.wait does not exist
24/06/04 17:11:43 ERROR Schema: Failed initialising database.
Unable to open a test connection to the given database. JDBC url = jdbc:derby:;databaseName=metastore_db;create=true, username = APP. Terminating connection pool (set lazyInit to true if you expect to start your database after your app). Original Exception: ------
java.sql.SQLException: Failed to start database 'metastore_db' with class loader jdk.internal.loader.ClassLoaders$AppClassLoader@5bc2b487, see the next exception for details.
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.Util.seeNextException(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.bootDatabase(Unknown Source)
	at org.a

AnalysisException: org.apache.hadoop.hive.ql.metadata.HiveException: java.lang.RuntimeException: Unable to instantiate org.apache.hadoop.hive.ql.metadata.SessionHiveMetaStoreClient

In [ ]:
artists_df = df.select(F.col('Artists')).distinct()
artists_list = [row['Artists'] for row in artists_df.collect()]

news_api_key = News_API.get('API_KEY')

news_data = []
for artist in artists_list:
    url = f"https://newsapi.org/v2/everything?q={artist}&pageSize=10&apiKey={news_api_key}"
    response = requests.get(url)
    if response.status_code == 200:
        articles = response.json()['articles']
        for article in articles:
            news_data.append({
                'Artist': artist,
                'Title': article.get('title'),
                'Description': article.get('description'),
                'URL': article.get('url'),
                'Content': article.get('content')
            })
    else:
        print(f"Failed to fetch news for artist: {artist}, Status Code: {response.status_code}")

news_df = pd.DataFrame(news_data)
news_spark_df = spark.createDataFrame(news_df)

news_spark_df.write.mode('overwrite').format('parquet').save('Mart/MusicFusion-Details')
news_spark_df.write.mode('overwrite').format('parquet').saveAsTable('MusicFusionDetails')

24/06/04 14:50:22 WARN MemoryManager: Total allocation exceeds 95.00% (1,020,054,720 bytes) of heap memory
Scaling row group sizes to 95.00% for 8 writers


In [ ]:
import pandas as pd
import requests
from pyspark.sql import SparkSession

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("Artist News Integration") \
    .enableHiveSupport() \
    .getOrCreate()

# Load the Parquet files into pandas DataFrames
apple_music_df = pd.read_parquet('/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/AppleMusic')
spotify_music_df = pd.read_parquet('/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/SpotifyMusic')
youtube_music_df = pd.read_parquet('/Users/ronitguptaaa/Documents/Music-Fusion-APP/Staging/YoutubeMusic')

# Normalize the artist name columns by stripping whitespace and converting to lower case
apple_music_df['artist_name_normalized'] = apple_music_df['Artist Name'].str.strip().str.lower()
spotify_music_df['artist_name_normalized'] = spotify_music_df['Artists'].str.strip().str.lower()
youtube_music_df['artist_name_normalized'] = youtube_music_df['Artist Name'].str.strip().str.lower()

# Perform the inner join between Apple Music and Spotify Music DataFrames
merged_df = pd.merge(apple_music_df, spotify_music_df, on='artist_name_normalized', how='inner')

# Perform the left join with YouTube Music DataFrame
final_df = pd.merge(merged_df, youtube_music_df, on='artist_name_normalized', how='left')

# Select the distinct artist names from the Spotify Music DataFrame
distinct_artists = final_df['Artists'].drop_duplicates()

# Convert the result to a pandas DataFrame
df = pd.DataFrame(distinct_artists, columns=['Artists'])

# Extract artist names as a list
artists_list = df['Artists'].tolist()

# NewsAPI key
news_api_key = 'YOUR_NEWSAPI_KEY'  # Replace with your actual NewsAPI key

# Function to fetch news for an artist
def fetch_news_for_artist(artist_name):
    url = f"https://newsapi.org/v2/everything?q={artist_name}&pageSize=10&apiKey={news_api_key}"
    response = requests.get(url)
    if response.status_code == 200:
        return response.json().get("articles", [])
    else:
        print(f"Failed to fetch news for artist: {artist_name}, Status Code: {response.status_code}")
        return []

# Fetch news for all artists and collect the results
news_data = []
for artist in artists_list:
    articles = fetch_news_for_artist(artist)
    for article in articles:
        news_data.append({
            'Artist': artist,
            'Title': article.get('title'),
            'Description': article.get('description'),
            'URL': article.get('url'),
            'Content': article.get('content')
        })

# Convert the list of articles into a pandas DataFrame
news_df = pd.DataFrame(news_data)

# Convert pandas DataFrame to Spark DataFrame
news_spark_df = spark.createDataFrame(news_df)

# Write the Spark DataFrame to Parquet and save as a Hive table
news_spark_df.write.mode('overwrite').format('parquet').save('/path/to/save/Mart/MusicFusion-Details')
news_spark_df.write.mode('overwrite').format('parquet').saveAsTable('MusicFusionDetails')

# Stop the Spark session
spark.stop()
